In [1]:
# pip install igraph

In [2]:
import pandas as pd
import numpy as np
import shapely
from shapely.geometry import LineString, Point
import random
from random import randrange

import geopandas as gpd 
from sklearn.neighbors import BallTree

from shapely.ops import nearest_points

import itertools
from operator import itemgetter
from scipy.spatial import cKDTree

import igraph as iG
import gc

from datetime import datetime 
from datetime import timedelta

import matplotlib.pyplot as plt

import re, math
import sys

import time

In [3]:
SEED = 2021
random.seed(SEED)

In [4]:
loc = "EGL-G_instances/"
dataset = "EGL-G"
comp_a = [1,2]
comp_b = ['A','B','C','D','E']

num_instances = 10
num_days = 1000

# The following parameters determine several key aspects of the simulation. The maximum value is *INclusive*. 
n_fac_min = 5
n_fac_max = 5    # the number of facilities present in the graph. 

facQ_min = 10
facQ_max = 10     # the number of vehicles (of any type) allowed to be simultaneously present at a facility. 
facQ = facQ_min  # this will be updated once set.

n_hosp_min = 1
n_hosp_max = 3    # . 

n_ALS_min = 5
n_ALS_max = 10   # the number of Advanced care vehicles

n_BLS_min = 15
n_BLS_max = 25    # the number of Basic/Standard care vehicles

n_CLS_min = 5
n_CLS_max = 10    # the number of Community care vehicles

Q_ALS = 1         # the number of patients an ALS vehicle can take to hospital
Q_BLS = 1         # the number of patients an BLS vehicle can take to hospital
Q_CLS = 0         # the number of patients an CLS vehicle can take to hospital

In [5]:
def get_map_name(curr_instance):
    if curr_instance == 0:
        return "EGL-G1-A"
    elif curr_instance == 1:
        return "EGL-G1-B"
    elif curr_instance == 2:
        return "EGL-G1-C"
    elif curr_instance == 3:
        return "EGL-G1-D"
    elif curr_instance == 4:
        return "EGL-G1-E"
    elif curr_instance == 5:
        return "EGL-G2-A"
    elif curr_instance == 6:
        return "EGL-G2-B"
    elif curr_instance == 7:
        return "EGL-G2-C"
    elif curr_instance == 8:
        return "EGL-G2-D"
    elif curr_instance == 9:
        return "EGL-G2-E"
    else:
        print("Broken map name request.")
        sys.exit()

# Let's begin by working with the street level data

First, we need to ensure that the graph is fully connected.

In [6]:
def get_times(df):
    times = []
    i = 0
    for index, row in df.iterrows():
        length = row[2]
        speed = 50
        
        vel = speed * 0.277778                  # turn it into m/s (i.e. velocity)
        time = math.ceil(length / vel) / 60     # length is already standardised to meters, convert to time (mins)
        times.append(time)  
        # print("We estimate it will take {} mins to travel {}m".format(time, length))
        i += 1
    
    return times

In [7]:
def next():
    global i1
    global i2
    global f
    global f_name
    
    if i1 > 1: 
        return -1
        
    file_loc = loc + dataset
    f_name = "{}{}-{}.dat".format(file_loc, comp_a[i1], comp_b[i2])
    f = open(f_name, "r")
    
    if i2 == 4:
        i2 = 0
        i1 += 1
    else: 
        i2 += 1  
        
    return 1

In [8]:
def get_data(file):
    lines = file.readlines()
    
    data = []
    
    curr = 9
    row = 0
    while curr < len(lines) - 1:
        line = lines[curr].split()
        val = int(line[3])
        if val > 0:
            to_add = [int(line[0]), int(line[1]), int(line[2])]
            to_add = [round(num, 0) for num in to_add]
            data.append(to_add)
            row += 1
        
        curr += 1
        
    return data

In [9]:
i1 = 0
i2 = 0
f = None
f_name = None

subgraphs = []
f_names = []

while next() > 0:
    data = get_data(f)
    df = pd.DataFrame(data)
    df[2] = get_times(df)
#     df = df.rename(columns={0: "head"})
#     df = df.rename(columns={1: "tail"})
    df = df.rename(columns={2: "time"})
    
#     df[0] = df.astype({'head': 'int32'}).dtypes
#     df[1] = df.astype({'tail': 'int32'}).dtypes
    
    tuples = [tuple(x) for x in df.values]
    
    subgraphs.append(iG.Graph.TupleList(tuples, directed = False, edge_attrs = ['time']))
    f_names.append(f_name)
    
# from here, step through the subgraphs (instances) in turn and output a metric tonne of additional data files 

In [10]:
print(len(subgraphs))

10


In [11]:
def sum_cost(subgraph, par_path):
    path = par_path
    curr = path[0]
    total_cost = 0
    for i in range(1, len(path), 1):
        arc_id = subgraph.get_eid(curr, path[i], directed=True, error=False)
        arc = subgraph.es[arc_id]
        total_cost += arc['time']

    return total_cost

In [12]:
def record_all_distances(f, subgraph): # this assumes a symmetrical graph
    prev_df = pd.DataFrame(np.zeros((subgraph.vcount(), subgraph.vcount())))
    time_df = pd.DataFrame(np.zeros((subgraph.vcount(), subgraph.vcount())))
    
    vs = subgraph.vs.indices
    
    for from_node in vs:
        out_paths = subgraph.get_all_shortest_paths(from_node, weights='time', mode='out') # path only
        
        for path in out_paths:
            to_node = path[len(path)-1]
            if len(path) > 1:
                prev = path[len(path)-2]
            else: 
                prev = to_node
            prev_df.iat[from_node, to_node] = prev
            path_cost = sum_cost(subgraph, path) # extract time cost of path
            time_df.iat[from_node, to_node] = path_cost
    
    # add the *sorted* node list as a row to the *start* of the matrix
    f.write(' '.join(map(str, sorted(vs))))
    f.write("\n")

    # strip the constructed dataframes of rows and columns containing only zeros (i.e. irrelevant nodes)
    prev_df = prev_df.loc[~(prev_df == 0).all(axis=1)]
    prev_df = prev_df.loc[:, (prev_df != 0).any(axis=0)]
    
    prev_df = prev_df.astype('int')
    
    for index, row in prev_df.iterrows():
        f.write(' '.join(map(str, row)))
        f.write('\n')

#     f.write(prev_df.to_string(index=False, header=False))
    f.write("\n---\n")

    time_df = time_df.loc[~(time_df == 0).all(axis=1)]
    time_df = time_df.loc[:, (time_df != 0).any(axis=0)]

    time_df = time_df.round(3)
    
    for index, row in time_df.iterrows():
        f.write(' '.join(map(str, row)))
        f.write('\n')
    
#     f.write(time_df.to_string(index=False, header=False))

In [13]:
def save_file():
    loc = "EGL-G_instances/"
    i = 0 
    while i < len(subgraphs):
        subgraph = subgraphs[i]
        f_name = loc + get_map_name(i) + ".txt"
        f_m = open(f_name, "w")

        num_arcs = subgraph.ecount()
        num_nodes = subgraph.vcount()

        f_m.write("name {}\n".format(get_map_name(i)))
        f_m.write("arcs {}\n".format(num_arcs))
        f_m.write("nodes {}\n".format(num_nodes))

        df = subgraph.get_edge_dataframe()

        for index, row in df.iterrows():
            row = "{} {} 0 {} 0 0 0 0".format(int(row[0]),int(row[1]),round(row[2], 3))
            f_m.write(row)
            f_m.write('\n')

        f_m.write('---\n')

        record_all_distances(f_m, subgraph)

        i += 1

In [14]:
# only un-comment if you intend to rebuild the entire map system i = 0 

# save_file()

# Now we can work with the call data

For Wellington data, this involves generating it from scratch.

In [15]:
def get_day(oldest, curr_day):
    new_day = oldest + timedelta(days=curr_day)

    new_hour = random.choices(np.arange(0, 24), [0.0246, 0.02109, 0.01908, 0.01756, 0.01641, 0.01852, 0.02274, 0.03439, 0.04377, 0.05159, 0.05867, 0.06097, 0.06181, 0.06263, 0.06229, 0.06062, 0.05893, 0.05725, 0.05402, 0.04956, 0.04382, 0.03900, 0.03269, 0.02796])
    new_minute = random.randint(0,59)
    new_day = new_day.replace(hour = new_hour[0], minute = new_minute)
    return new_day

In [16]:
oldest = datetime(2015, 1, 1) # this doesn't actually matter. As long as there are %10 = 0 
curr_day = 0
calls = []

# mu = 11/60 * 24 (WFA experiences, on average, 11 calls per minute, 24/7)
# sigma = 130 * 0.2, as a 20% daily SD was observed in the Marin dataset. 
# SD will likely be modified once we receive better data. 
mu, sigma = 130, 26
# values = Generator.normal(loc=mu, scale=sigma, size=num_days)

curr_inst = 0
while curr_inst < num_instances:
    d = 0
    inst_calls = []
    
    rng = np.random.default_rng(SEED)
    gen_values = rng.normal(mu, sigma, num_days)
    # gen_values = random.normal(mu, sigma, num_days)

    values = [] # frustrating, but have to convert from float to int.
    for i in range(len(gen_values)):
        values.append(int(gen_values[i]))

    for i in range(num_days):
        daily_calls = values[0]

        day_calls = []
        for j in range(daily_calls):
            call = get_day(oldest, curr_day)
            day_calls.append(call)
        curr_day += 1

        day_calls = pd.DataFrame(day_calls)
        day_calls = day_calls.rename(columns={0: "c_m"})

        inst_calls.append(day_calls)
        
    calls.append(inst_calls)
    curr_inst += 1

In [17]:
# print((calls[1][0]))

In [18]:
def get_arcs(calls, arcs):
    heads = []
    tails = []
    for index, row in calls.iterrows(): # only iterating over the number of calls
        arc = random.sample(arcs,1)
        heads.append(arc[0][0])
        tails.append(arc[0][1])
    return heads,tails

In [19]:
i = 0
while i < num_instances:
    d = 0
    while d < num_days:
        heads, tails = get_arcs(calls[i][d], subgraphs[i].get_edgelist())
        calls[i][d]['head'] = heads
        calls[i][d]['tail'] = tails
        d += 1
    i += 1

In [20]:
calls[1][0].head() 

c_m  head  tail
0 2017-09-27 10:13:00   141   142
1 2017-09-27 09:58:00     0     1
2 2017-09-27 06:45:00     4    22
3 2017-09-27 19:04:00   196   203
4 2017-09-27 04:15:00   188   189

In [21]:
def frac_iter(df):
    frac = []
    for index, row in df.iterrows():
        frac.append(random.uniform(0,1))
    return frac

In [22]:
i = 0
while i < num_instances:
    d = 0
    while d < num_days:
        calls[i][d] = pd.DataFrame(calls[i][d])
        calls[i][d]['c_af'] = frac_iter(calls[i][d])
        d += 1
    i += 1

In [23]:
calls[1][0].head() 

c_m  head  tail      c_af
0 2017-09-27 10:13:00   141   142  0.951416
1 2017-09-27 09:58:00     0     1  0.912258
2 2017-09-27 06:45:00     4    22  0.861383
3 2017-09-27 19:04:00   196   203  0.298932
4 2017-09-27 04:15:00   188   189  0.606417

In [24]:
def treat_iter(df):
    time = []
    for index, row in df.iterrows():
        time.append(random.randint(20,40))
    return time

In [25]:
i = 0
while i < num_instances:
    d = 0
    while d < num_days:
        calls[i][d]['c_tau'] = treat_iter(calls[i][d])
        d += 1
    i += 1

In [26]:
bound_1 = 0.02
bound_2 = 0.42 + bound_1
bound_3 = 0.45 + bound_2

def dem_iter(df):
    dem = []
    for index, row in df.iterrows():
        first = random.uniform(0,1)
        if first <= bound_1:
            second = random.randint(0,1)
            if second == 0: 
                dem.append('{1,3,0}')
            else:
                dem.append('{1,2,0}')
        elif first <= bound_2:
            second = random.randint(0,2)
            if second == 0:
                dem.append('{1,1,0}')
            elif second == 1:
                dem.append('{1,0,0}')
            else:
                dem.append('{0,3,0}')
        elif first <= bound_3:
            second = random.randint(0,1)
            if second == 0:
                dem.append('{0,2,0}')
            else:
                dem.append('{0,1,0}')
        else:
            second = random.randint(0,1)
            if second == 0:
                dem.append('{0,1,1}')
            else:
                dem.append('{0,0,1}')
    return dem

In [27]:
i = 0
while i < num_instances:
    d = 0
    while d < num_days:
        calls[i][d]['c_d'] = dem_iter(calls[i][d])
        d += 1
    i += 1

In [28]:
def hosp_iter(df):
    hosp = []
    highest_priority = ['{1,3,0}','{1,2,0}','{1,1,0}','{1,0,0}']
    
    for index, row in df.iterrows():
        go_to_hosp = -1
        frac = random.uniform(0,1)
        if row['c_d'] in highest_priority:
            if frac < 0.95:
                go_to_hosp = 1
            else: 
                go_to_hosp = 0
        else:
            if frac < 0.6:
                go_to_hosp = 1
            else:
                go_to_hosp = 0
        hosp.append(go_to_hosp)
    return hosp

In [29]:
i = 0
while i < num_instances:
    d = 0
    while d < num_days:
        calls[i][d]['c_h'] = hosp_iter(calls[i][d])
        calls[i][d] = calls[i][d].sort_values(by='c_m')
        d += 1
    i += 1

In [30]:
calls[1][1]

c_m  head  tail      c_af  c_tau      c_d  c_h
17  2017-09-28 00:10:00    63    64  0.046921     35  {0,3,0}    0
59  2017-09-28 00:17:00   243   244  0.867624     34  {0,1,0}    0
21  2017-09-28 00:19:00    28    29  0.906836     35  {0,2,0}    1
2   2017-09-28 00:36:00    85    86  0.200811     27  {1,1,0}    1
64  2017-09-28 00:45:00    36    39  0.019203     20  {0,1,0}    1
..                  ...   ...   ...       ...    ...      ...  ...
30  2017-09-28 22:40:00   132   134  0.613216     39  {0,1,1}    1
103 2017-09-28 22:43:00    88    96  0.922506     24  {0,1,1}    1
109 2017-09-28 23:30:00    28    29  0.954265     37  {0,1,0}    1
51  2017-09-28 23:37:00   153   156  0.122714     24  {1,2,0}    1
117 2017-09-28 23:57:00   151   152  0.608339     31  {0,3,0}    1

[128 rows x 7 columns]

In [31]:
i = 0
while i < num_instances:
    d = 0
    while d < num_days:
        calls[i][d] = calls[i][d].reindex(columns=['c_m','head','tail','c_af','c_d','c_tau','c_h'])
        d += 1
    i += 1

calls[1][0].head()

c_m  head  tail      c_af      c_d  c_tau  c_h
48  2017-09-27 00:02:00   178   183  0.198351  {0,3,0}     40    1
15  2017-09-27 00:42:00   222   225  0.943457  {0,2,0}     22    1
40  2017-09-27 01:01:00   202   204  0.195721  {0,1,0}     32    1
104 2017-09-27 01:54:00   150   151  0.982605  {0,2,0}     33    0
18  2017-09-27 02:02:00    50    53  0.244986  {0,2,0}     26    0

# Right, let's start finalising this dataset 

#### Now we are starting to finalise and save the call data.

In [32]:
def path_loop(res, union, paths):
    for path in paths:
        for node in path:
            if node not in union:
                res.add(node) # sets can't have duplicates, so just add. 

In [33]:
def unionish(child_list, parent_list, paths_A, paths_B, paths_C):
    union = set.union(set(child_list), set(parent_list)) # to exclude duplicates
    
    res = set()
    path_loop(res, union, paths_A) # now let's find the new nodes
    path_loop(res, union, paths_B)
    path_loop(res, union, paths_C)
    
    return sorted(res), sorted(union)

In [34]:
def dijkstras(listA, listB, prev_df, time_df, subgraph):
    listA = [int(x) for x in listA]
    listB = [int(x) for x in listB]
    
    res_paths = []
    for ele in listA:
        out_paths = subgraph.get_shortest_paths(ele, listB, weights='time', mode='out', output='vpath') # path only
        
        for path in out_paths:
            res_paths.append(path)
            this = path[len(path)-1]
            if len(path) > 1:
                prev = path[len(path)-2]
            else: 
                prev = this
            prev_df.iat[ele, this] = prev
            path_cost = sum_cost(subgraph, path) # extract time cost of path
            time_df.iat[ele, this] = path_cost
        
    return prev_df, time_df, res_paths

In [35]:
def record_distances(parent_list, child_list, prev_df, time_df, subgraph):
    print(f"Parent: {len(parent_list)}. Child: {len(child_list)}")
    prev_df, time_df, paths_A = dijkstras(child_list, parent_list, prev_df, time_df, subgraph)  # bottom left
    prev_df, time_df, paths_B = dijkstras(parent_list, child_list, prev_df, time_df, subgraph)  # top right
    prev_df, time_df, paths_C = dijkstras(child_list, child_list, prev_df, time_df, subgraph)   # bottom right
    
    child_list, parent_list = unionish(child_list, parent_list, paths_A, paths_B, paths_C)
    
    if len(child_list) > 0:
        return record_distances(parent_list, child_list, prev_df, time_df, subgraph)
    else:
        return prev_df, time_df, parent_list

In [36]:
def manage_record_distances(f, subgraph, parent_nodes):
    parent_list = sorted(parent_nodes)
    
    prev_df = pd.DataFrame(np.zeros((subgraph.vcount(), subgraph.vcount())))
    time_df = pd.DataFrame(np.zeros((subgraph.vcount(), subgraph.vcount())))

    prev_df, time_df, paths_a = dijkstras(parent_list, parent_list, prev_df, time_df, subgraph)  # i to j
    res = set()
    path_loop(res, set(parent_list), paths_a)
    child_list = sorted(res)

    prev_df, time_df, save_parents = record_distances(parent_list, child_list, prev_df, time_df, subgraph)
    
    save_parents = list(map(int, save_parents))
    
    # add the *sorted* node list as a row to the *start* of the matrix
    f.write(' '.join(map(str, sorted(save_parents))))
    f.write("\n")

    # strip the constructed dataframes of rows and columns containing only zeros (i.e. irrelevant nodes)
    prev_df = prev_df.loc[~(prev_df == 0).all(axis=1)]
    prev_df = prev_df.loc[:, (prev_df != 0).any(axis=0)]
    
    prev_df = prev_df.astype('int')

    f.write(prev_df.to_string(index=False, header=False))
    f.write("\n---\n")

    time_df = time_df.loc[~(time_df == 0).all(axis=1)]
    time_df = time_df.loc[:, (time_df != 0).any(axis=0)]

    time_df = time_df.round(3)
    
    f.write(time_df.to_string(index=False, header=False))

In [37]:
# turns an annoying hr:min:sec:ms format into a round number of minutes.
def to_sheer_minutes(time):
    return time.hour * 60 + time.minute

In [38]:
def add_rand_nodes(base_str, num_needed, G):
    edge_df = G.get_edge_dataframe()
    
    nodes = []
    maximum = len(edge_df) - 1 
    node = 0
    for i in range(num_needed):
        pick = random.randint(0, maximum)
        while node in nodes:
            pick = random.randint(0, maximum) 
            row = edge_df.iloc[pick]

            if random.randint(0,1) == 0:
                node = row['source']
            else: 
                node = row['target']
            
        node = int(node)
        nodes.append(node) 
        base_str += str(node)
        
        if i < num_needed - 1:
            base_str += ','
            
    return base_str + '}\n', nodes

In [39]:
def rand_loc_veh(alloc, valid, base_str, n_veh, fac, facQ):
    this_alloc = np.zeros(len(fac))
    while sum(this_alloc) < n_veh: 
        rand_index = random.randint(0, len(valid) - 1)
        rand_fac = valid[rand_index]
        index = fac.index(rand_fac)
        
#         while(alloc[index] >= facQ):      # we must avoid overloading a facility in the first instance! 
#             rand_fac = random.choice(fac)
#             index = fac.index(rand_fac)    
        
        alloc[index] += 1
        this_alloc[index] += 1
        
        if alloc[index] == facQ:
            valid.remove(rand_fac)
            
    num_pos = np.sum(np.array(this_alloc) > 0, axis=0)
    curr_pos = 0
    
    for i in range(len(fac)):
        if this_alloc[i] > 0:
            base_str += '{}:{}'.format(int(this_alloc[i]),fac[i])
            if curr_pos < num_pos - 1: 
                base_str += ','
                curr_pos += 1
            
    return base_str + '}\n'

In [40]:
def save_data(f, calls, G, curr_instance): 
    # instance parameters
    n_fac = random.randint(n_fac_min, n_fac_max)
    facQ = random.randint(facQ_min, facQ_max)
    n_hosp = random.randint(n_hosp_min, n_hosp_max)
    n_ALS = random.randint(n_ALS_min, n_ALS_max)
    n_BLS = random.randint(n_BLS_min, n_BLS_max)
    n_CLS = random.randint(n_CLS_min, n_CLS_max)
    
    fac_str = 'fac {} {} {{'.format(n_fac, facQ)
    hosp_str = 'hosp {} {{'.format(n_hosp)
    ALS_str = 'n_ALS {} {} {{'.format(n_ALS,Q_ALS)
    BLS_str = 'n_BLS {} {} {{'.format(n_BLS,Q_BLS)
    CLS_str = 'n_CLS {} {} {{'.format(n_CLS,Q_CLS)    

    fac_str, facilities = add_rand_nodes(fac_str, n_fac, G)
    hosp_str, hospitals = add_rand_nodes(hosp_str, n_hosp, G)
    
    alloc = np.zeros(len(facilities)) 
    alloc = alloc.astype('int')
    alloc = alloc.tolist()
    valid = []
    valid.extend(facilities)

    ALS_str = rand_loc_veh(alloc, valid, ALS_str, n_ALS, facilities, facQ)
    BLS_str = rand_loc_veh(alloc, valid, BLS_str, n_BLS, facilities, facQ)
    CLS_str = rand_loc_veh(alloc, valid, CLS_str, n_CLS, facilities, facQ)
    
    f.write('map {}\n'.format(get_map_name(curr_instance)))
    f.write(fac_str)
    f.write(hosp_str)
    f.write(ALS_str)
    f.write(BLS_str)
    f.write(CLS_str)
    
    calls_df = pd.DataFrame(calls, columns=['c_m','head','tail','c_af','c_d','c_tau','c_h'])
    f.write(calls_df.to_string() + '\n')
    
#     call_nodes = set()
#     for index, row in calls_df.iterrows():
#         call_nodes.add(row['head'])
#         call_nodes.add(row['tail'])
            
#     parent_nodes = set()
#     parent_nodes.update(call_nodes)
#     parent_nodes.update(facilities)
#     parent_nodes.update(hospitals)

In [41]:
def save_iter(calls, G, save_index, curr_instance):
    save_me = []
    curr = None
    df_vals = []
    for index, row in calls.iterrows():
        this = row['c_m']
        row['c_m'] = to_sheer_minutes(this)
        df_vals.append(row)
        
    file_name = "{}_instances/{}_{}.txt".format(dataset,dataset,save_index)
    f = open(file_name,"a")
    save_data(f, pd.DataFrame(df_vals), G, curr_instance)

    curr = this
    df_vals = []
    save_me.append(row)

In [42]:
i = 0
file_index = 0
while i < num_instances:
    subgraph = subgraphs[i]
    d = 0
    while d < num_days:
        save_iter(calls[i][d], subgraph, file_index, i)
        d += 1
        file_index += 1
    i += 1

picking: 0
picking: 137
picking: 176
picking: 181
picking: 49
picking: 0
a9 b16 c8
[0, 137, 176, 181, 49]
[0, 137, 176, 181, 49]
[0, 0, 0, 0, 0]
[1, 2, 1, 2, 3]
[0, 137, 176, 181, 49]
[7, 4, 3, 3, 8]
[0, 137, 176, 181, 49]
[9, 4, 4, 6, 10]
[0, 137, 176, 181]
picking: 0
picking: 216
picking: 89
picking: 49
picking: 233
picking: 0
a7 b16 c8
[0, 216, 89, 49, 233]
[0, 216, 89, 49, 233]
[0, 0, 0, 0, 0]
[2, 1, 1, 3, 0]
[0, 216, 89, 49, 233]
[5, 2, 3, 5, 8]
[0, 216, 89, 49, 233]
[6, 4, 5, 6, 10]
[0, 216, 89, 49]
picking: 0
picking: 132
picking: 245
picking: 246
picking: 152
picking: 0
picking: 217
a9 b23 c7
[0, 132, 245, 246, 152]
[0, 132, 245, 246, 152]
[0, 0, 0, 0, 0]
[2, 2, 0, 4, 1]
[0, 132, 245, 246, 152]
[7, 7, 1, 10, 7]
[0, 132, 245, 152]
[10, 8, 2, 10, 9]
[132, 245, 152]
picking: 0
picking: 232
picking: 115
picking: 213
picking: 125
picking: 0
a5 b19 c8
[0, 232, 115, 213, 125]
[0, 232, 115, 213, 125]
[0, 0, 0, 0, 0]
[0, 2, 0, 2, 1]
[0, 232, 115, 213, 125]
[3, 6, 2, 6, 7]
[0, 232, 115, 

picking: 0
picking: 114
picking: 192
picking: 4
picking: 199
picking: 0
picking: 79
picking: 123
a6 b20 c8
[0, 114, 192, 4, 199]
[0, 114, 192, 4, 199]
[0, 0, 0, 0, 0]
[4, 0, 0, 1, 1]
[0, 114, 192, 4, 199]
[4, 4, 6, 4, 8]
[0, 114, 192, 4, 199]
[5, 6, 7, 6, 10]
[0, 114, 192, 4]
picking: 0
picking: 186
picking: 1
picking: 94
picking: 104
picking: 0
picking: 233
a7 b15 c10
[0, 186, 1, 94, 104]
[0, 186, 1, 94, 104]
[0, 0, 0, 0, 0]
[0, 3, 2, 1, 1]
[0, 186, 1, 94, 104]
[4, 7, 3, 3, 5]
[0, 186, 1, 94, 104]
[5, 8, 5, 8, 6]
[0, 186, 1, 94, 104]
picking: 0
picking: 15
picking: 111
picking: 175
picking: 228
picking: 0
picking: 139
a10 b20 c9
[0, 15, 111, 175, 228]
[0, 15, 111, 175, 228]
[0, 0, 0, 0, 0]
[0, 1, 1, 5, 3]
[0, 15, 111, 175, 228]
[7, 3, 6, 10, 4]
[0, 15, 111, 228]
[9, 4, 8, 10, 8]
[0, 15, 111, 228]
picking: 0
picking: 121
picking: 83
picking: 25
picking: 179
picking: 0
a5 b18 c9
[0, 121, 83, 25, 179]
[0, 121, 83, 25, 179]
[0, 0, 0, 0, 0]
[1, 0, 1, 2, 1]
[0, 121, 83, 25, 179]
[4, 3, 4, 5

picking: 0
picking: 117
picking: 68
picking: 86
picking: 130
picking: 0
picking: 18
a10 b21 c8
[0, 117, 68, 86, 130]
[0, 117, 68, 86, 130]
[0, 0, 0, 0, 0]
[3, 4, 2, 1, 0]
[0, 117, 68, 86, 130]
[5, 6, 5, 5, 10]
[0, 117, 68, 86]
[6, 10, 8, 5, 10]
[0, 68, 86]
picking: 0
picking: 232
picking: 82
picking: 4
picking: 17
picking: 0
a10 b24 c10
[0, 232, 82, 4, 17]
[0, 232, 82, 4, 17]
[0, 0, 0, 0, 0]
[1, 2, 1, 2, 4]
[0, 232, 82, 4, 17]
[4, 7, 9, 8, 6]
[0, 232, 82, 4, 17]
[6, 8, 10, 10, 10]
[0, 232]
picking: 0
picking: 178
picking: 91
picking: 43
picking: 107
picking: 0
picking: 14
a7 b23 c10
[0, 178, 91, 43, 107]
[0, 178, 91, 43, 107]
[0, 0, 0, 0, 0]
[2, 1, 0, 1, 3]
[0, 178, 91, 43, 107]
[9, 4, 5, 7, 5]
[0, 178, 91, 43, 107]
[10, 6, 7, 9, 8]
[178, 91, 43, 107]
picking: 0
picking: 107
picking: 70
picking: 104
picking: 249
picking: 0
picking: 95
picking: 26
a10 b23 c8
[0, 107, 70, 104, 249]
[0, 107, 70, 104, 249]
[0, 0, 0, 0, 0]
[2, 2, 1, 3, 2]
[0, 107, 70, 104, 249]
[9, 7, 4, 10, 3]
[0, 107, 70,

picking: 0
picking: 244
picking: 147
picking: 145
picking: 117
picking: 0
picking: 139
picking: 28
a7 b18 c5
[0, 244, 147, 145, 117]
[0, 244, 147, 145, 117]
[0, 0, 0, 0, 0]
[1, 1, 1, 2, 2]
[0, 244, 147, 145, 117]
[4, 5, 5, 4, 7]
[0, 244, 147, 145, 117]
[6, 5, 7, 4, 8]
[0, 244, 147, 145, 117]
picking: 0
picking: 226
picking: 136
picking: 23
picking: 13
picking: 0
a7 b17 c9
[0, 226, 136, 23, 13]
[0, 226, 136, 23, 13]
[0, 0, 0, 0, 0]
[0, 4, 0, 1, 2]
[0, 226, 136, 23, 13]
[3, 6, 6, 4, 5]
[0, 226, 136, 23, 13]
[6, 7, 7, 4, 9]
[0, 226, 136, 23, 13]
picking: 0
picking: 40
picking: 119
picking: 249
picking: 141
picking: 0
picking: 14
a10 b25 c7
[0, 40, 119, 249, 141]
[0, 40, 119, 249, 141]
[0, 0, 0, 0, 0]
[5, 0, 2, 1, 2]
[0, 40, 119, 249, 141]
[9, 3, 8, 9, 6]
[0, 40, 119, 249, 141]
[10, 5, 10, 9, 8]
[40, 249, 141]
picking: 0
picking: 222
picking: 249
picking: 90
picking: 2
picking: 0
a10 b19 c5
[0, 222, 249, 90, 2]
[0, 222, 249, 90, 2]
[0, 0, 0, 0, 0]
[2, 3, 2, 3, 0]
[0, 222, 249, 90, 2]
[6, 9

picking: 0
picking: 75
picking: 232
picking: 56
picking: 227
picking: 0
picking: 28
a5 b19 c10
[0, 75, 232, 56, 227]
[0, 75, 232, 56, 227]
[0, 0, 0, 0, 0]
[2, 2, 0, 1, 0]
[0, 75, 232, 56, 227]
[7, 5, 3, 5, 4]
[0, 75, 232, 56, 227]
[8, 9, 6, 6, 5]
[0, 75, 232, 56, 227]
picking: 0
picking: 240
picking: 35
picking: 187
picking: 52
picking: 0
picking: 144
a8 b20 c6
[0, 240, 35, 187, 52]
[0, 240, 35, 187, 52]
[0, 0, 0, 0, 0]
[2, 2, 2, 1, 1]
[0, 240, 35, 187, 52]
[9, 5, 6, 4, 4]
[0, 240, 35, 187, 52]
[10, 5, 7, 4, 8]
[240, 35, 187, 52]
picking: 0
picking: 209
picking: 100
picking: 84
picking: 141
picking: 0
picking: 216
picking: 22
a6 b16 c7
[0, 209, 100, 84, 141]
[0, 209, 100, 84, 141]
[0, 0, 0, 0, 0]
[0, 1, 1, 3, 1]
[0, 209, 100, 84, 141]
[3, 3, 4, 6, 6]
[0, 209, 100, 84, 141]
[5, 3, 6, 9, 6]
[0, 209, 100, 84, 141]
picking: 0
picking: 82
picking: 152
picking: 38
picking: 175
picking: 0
picking: 117
a9 b19 c7
[0, 82, 152, 38, 175]
[0, 82, 152, 38, 175]
[0, 0, 0, 0, 0]
[2, 1, 2, 2, 2]
[0, 82

...

picking: 0
picking: 74
picking: 152
picking: 147
picking: 124
picking: 0
a8 b21 c5
[0, 74, 152, 147, 124]
[0, 74, 152, 147, 124]
[0, 0, 0, 0, 0]
[3, 2, 3, 0, 0]
[0, 74, 152, 147, 124]
[10, 4, 8, 3, 4]
[74, 152, 147, 124]
[10, 5, 9, 6, 4]
[74, 152, 147, 124]
picking: 0
picking: 179
picking: 40
picking: 247
picking: 19
picking: 0
picking: 196
picking: 218
a9 b16 c8
[0, 179, 40, 247, 19]
[0, 179, 40, 247, 19]
[0, 0, 0, 0, 0]
[3, 1, 2, 2, 1]
[0, 179, 40, 247, 19]
[10, 3, 6, 3, 3]
[179, 40, 247, 19]
[10, 6, 9, 3, 5]
[179, 40, 247, 19]
picking: 0
picking: 66
picking: 163
picking: 172
picking: 200
picking: 0
a7 b17 c5
[0, 66, 163, 172, 200]
[0, 66, 163, 172, 200]
[0, 0, 0, 0, 0]
[1, 1, 3, 0, 2]
[0, 66, 163, 172, 200]
[3, 4, 6, 2, 9]
[0, 66, 163, 172, 200]
[4, 7, 7, 2, 9]
[0, 66, 163, 172, 200]
picking: 0
picking: 36
picking: 70
picking: 5
picking: 155
picking: 0
picking: 155
a9 b25 c5
[0, 36, 70, 5, 155]
[0, 36, 70, 5, 155]
[0, 0, 0, 0, 0]
[2, 1, 3, 2, 1]
[0, 36, 70, 5, 155]
[8, 7, 10, 5, 4]


picking: 0
picking: 112
picking: 141
a6 b22 c9
[0, 167, 79, 192, 245]
[0, 167, 79, 192, 245]
[0, 0, 0, 0, 0]
[0, 0, 0, 3, 3]
[0, 167, 79, 192, 245]
[5, 2, 2, 9, 10]
[0, 167, 79, 192]
[5, 6, 6, 10, 10]
[0, 167, 79]
picking: 0
picking: 8
picking: 1
picking: 61
picking: 242
picking: 0
picking: 172
picking: 229
a7 b15 c7
[0, 8, 1, 61, 242]
[0, 8, 1, 61, 242]
[0, 0, 0, 0, 0]
[2, 1, 1, 3, 0]
[0, 8, 1, 61, 242]
[4, 6, 5, 5, 2]
[0, 8, 1, 61, 242]
[4, 6, 9, 6, 4]
[0, 8, 1, 61, 242]
picking: 0
picking: 128
picking: 165
picking: 77
picking: 65
picking: 0
picking: 202
a10 b20 c10
[0, 128, 165, 77, 65]
[0, 128, 165, 77, 65]
[0, 0, 0, 0, 0]
[1, 3, 2, 4, 0]
[0, 128, 165, 77, 65]
[6, 4, 9, 8, 3]
[0, 128, 165, 77, 65]
[6, 6, 10, 10, 8]
[0, 128, 65]
picking: 0
picking: 20
picking: 40
picking: 181
picking: 49
picking: 0
a9 b17 c7
[0, 20, 40, 181, 49]
[0, 20, 40, 181, 49]
[0, 0, 0, 0, 0]
[1, 1, 2, 3, 2]
[0, 20, 40, 181, 49]
[4, 3, 7, 6, 6]
[0, 20, 40, 181, 49]
[5, 4, 10, 7, 7]
[0, 20, 181, 49]
picking: 0


picking: 0
picking: 37
picking: 67
a7 b18 c10
[0, 95, 28, 74, 87]
[0, 95, 28, 74, 87]
[0, 0, 0, 0, 0]
[1, 0, 2, 1, 3]
[0, 95, 28, 74, 87]
[4, 5, 8, 1, 7]
[0, 95, 28, 74, 87]
[9, 6, 9, 3, 8]
[0, 95, 28, 74, 87]
picking: 0
picking: 152
picking: 138
picking: 6
picking: 131
picking: 0
picking: 80
a7 b15 c7
[0, 152, 138, 6, 131]
[0, 152, 138, 6, 131]
[0, 0, 0, 0, 0]
[0, 1, 2, 1, 3]
[0, 152, 138, 6, 131]
[3, 6, 3, 4, 6]
[0, 152, 138, 6, 131]
[6, 8, 4, 5, 6]
[0, 152, 138, 6, 131]
picking: 0
picking: 34
picking: 37
picking: 143
picking: 161
picking: 0
a7 b25 c8
[0, 34, 37, 143, 161]
[0, 34, 37, 143, 161]
[0, 0, 0, 0, 0]
[1, 1, 1, 3, 1]
[0, 34, 37, 143, 161]
[6, 5, 7, 7, 7]
[0, 34, 37, 143, 161]
[7, 7, 8, 10, 8]
[0, 34, 37, 161]
picking: 0
picking: 127
picking: 83
picking: 133
picking: 74
picking: 0
picking: 30
a10 b25 c8
[0, 127, 83, 133, 74]
[0, 127, 83, 133, 74]
[0, 0, 0, 0, 0]
[3, 3, 1, 2, 1]
[0, 127, 83, 133, 74]
[9, 7, 8, 7, 4]
[0, 127, 83, 133, 74]
[9, 9, 9, 7, 9]
[0, 127, 83, 133, 74]
p

picking: 0
picking: 115
picking: 201
picking: 172
picking: 230
picking: 0
a7 b21 c7
[0, 115, 201, 172, 230]
[0, 115, 201, 172, 230]
[0, 0, 0, 0, 0]
[1, 1, 2, 2, 1]
[0, 115, 201, 172, 230]
[6, 4, 6, 5, 7]
[0, 115, 201, 172, 230]
[7, 5, 7, 6, 10]
[0, 115, 201, 172]
picking: 0
picking: 24
picking: 159
picking: 64
picking: 52
picking: 0
picking: 250
a6 b17 c9
[0, 24, 159, 64, 52]
[0, 24, 159, 64, 52]
[0, 0, 0, 0, 0]
[3, 0, 1, 1, 1]
[0, 24, 159, 64, 52]
[6, 2, 8, 4, 3]
[0, 24, 159, 64, 52]
[8, 4, 8, 6, 6]
[0, 24, 159, 64, 52]
picking: 0
picking: 95
picking: 108
picking: 71
picking: 45
picking: 0
a9 b20 c9
[0, 95, 108, 71, 45]
[0, 95, 108, 71, 45]
[0, 0, 0, 0, 0]
[2, 1, 2, 4, 0]
[0, 95, 108, 71, 45]
[9, 3, 6, 5, 6]
[0, 95, 108, 71, 45]
[10, 4, 7, 8, 9]
[95, 108, 71, 45]
picking: 0
picking: 135
picking: 177
picking: 28
picking: 56
picking: 0
a8 b25 c10
[0, 135, 177, 28, 56]
[0, 135, 177, 28, 56]
[0, 0, 0, 0, 0]
[3, 0, 2, 2, 1]
[0, 135, 177, 28, 56]
[5, 4, 8, 10, 6]
[0, 135, 177, 56]
[9, 7, 10

picking: 0
picking: 176
picking: 90
picking: 237
picking: 249
picking: 0
picking: 123
picking: 42
a8 b17 c8
[0, 176, 90, 237, 249]
[0, 176, 90, 237, 249]
[0, 0, 0, 0, 0]
[3, 1, 1, 1, 2]
[0, 176, 90, 237, 249]
[5, 6, 4, 6, 4]
[0, 176, 90, 237, 249]
[5, 7, 7, 9, 5]
[0, 176, 90, 237, 249]
